In [6]:
import pandas as pd

In [2]:
import sys, os


In [3]:
print("kernel python :", sys.executable)


kernel python : /opt/homebrew/Caskroom/miniconda/base/bin/python


In [4]:
print("env name      :", os.environ.get("CONDA_DEFAULT_ENV"))
タ

env name      : base


NameError: name 'タ' is not defined

In [5]:
print("env name      :", os.environ.get("CONDA_DEFAULT_ENV"))


env name      : base


In [1]:
df = pd.read_csv("activities.csv", parse_dates=["start_date"])

NameError: name 'pd' is not defined

In [2]:
import pandas as pd

In [3]:
df = pd.read_csv("activities.csv", parse_dates=["start_date"])

FileNotFoundError: [Errno 2] No such file or directory: 'activities.csv'

In [4]:
pwd

'/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ'

In [7]:
df = pd.read_csv("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/StravaData/activities.csv", parse_dates=["start_date"])

ValueError: Missing column provided to 'parse_dates': 'start_date'

In [12]:
# ============================================================
# Strava 日本語ヘッダー → 英語ヘッダー　一括変換スクリプト
# Jupyter Notebook 用（セル 1 発で完結）
# ============================================================

import pandas as pd
from pathlib import Path

# ▼ 変換対象ファイル
SRC = Path("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/StravaData/activities.csv")       # 日本語ヘッダー CSV
DST = Path("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/StravaData/activities.csv")    # 出力先（英語ヘッダー CSV）

# ▼ 日本語 → 英語 マッピング辞書
JP2EN = {
    # ==== 基本情報 ====
    "アクティビティID": "Activity ID",
    "アクティビティ実行日": "Activity Date",
    "アクティビティ名": "Activity Name",
    "アクティビティタイプ": "Activity Type",
    "アクティビティの説明": "Description",
    "経過時間": "Elapsed Time",
    "移動時間": "Moving Time",
    "距離": "Distance",
    "開始時間": "Start Time",
    "タイプ": "Device Type",
    "アクティビティのプライベートメモ": "Activity Private Notes",
    "アクティビティギア": "Gear",
    "ギア": "Gear",
    "ファイル名": "Filename",
    # ==== 心拍・パワー ====
    "最大心拍数": "Max Heart Rate",
    "平均心拍数": "Average Heart Rate",
    "最大ワット": "Max Power",
    "平均ワット": "Average Power",
    "加重平均パワー": "Weighted Average Power",
    "パワーカウント": "Power Count",
    # ==== スピード・距離 ====
    "最高速度": "Max Speed",
    "平均速度": "Average Speed",
    "平均経過スピード": "Average Elapsed Speed",
    "Grade Adjusted Pace": "Grade Adjusted Pace",
    "Grade Adjusted Pace (平均)": "Grade Adjusted Pace (Average)",
    # ==== 標高・勾配 ====
    "獲得標高": "Elevation Gain",
    "獲得標高（下り）": "Elevation Loss",
    "最低標高": "Min Elevation",
    "最高標高": "Max Elevation",
    "最大勾配": "Max Grade",
    "平均勾配": "Average Grade",
    "平均プラス勾配": "Average Positive Grade",
    "平均マイナス勾配": "Average Negative Grade",
    # ==== ケイデンス ====
    "最大ケイデンス": "Max Cadence",
    "平均ケイデンス": "Average Cadence",
    # ==== エフォート／負荷 ====
    "相対的エフォート": "Relative Effort",
    "主観的相対的エフォート": "Perceived Relative Effort",
    "主観的運動強度": "Perceived Exertion",
    "主観的運動強度を使用する": "Perceived Exertion Used",
    "合計運動量": "Total Work",
    "トレーニングロード": "Training Load",
    "強度": "Intensity",
    # ==== 時間内訳 ====
    "上り坂のタイム": "Uphill Time",
    "下り坂のタイム": "Downhill Time",
    "その他のタイム": "Other Time",
    "タイマー時間": "Timer Time",
    # ==== 体重・重量 ====
    "アスリート体重": "Athlete Weight",
    "自転車重量": "Bike Weight",
    "総重量": "Total Weight",
    # ==== 温度・気象 ====
    "最高気温": "Max Temperature",
    "平均気温": "Average Temperature",
    "体感温度": "Apparent Temperature",
    "露点": "Dew Point",
    "湿度": "Humidity",
    "気圧": "Pressure",
    "天候": "Weather",
    "観測時刻": "Observation Time",
    "風速": "Wind Speed",
    "瞬間風速": "Wind Gust",
    "風向": "Wind Bearing",
    "降水量": "Precipitation",
    "降水確率": "Precipitation Probability",
    "降水タイプ": "Precipitation Type",
    "雲量": "Cloud Cover",
    "視程": "Visibility",
    "UV指数": "UV Index",
    "オゾン情報": "Ozone",
    "日の出": "Sunrise Time",
    "日の入": "Sunset Time",
    "月齢": "Moon Phase",
    # ==== ルート特有 ====
    "ジャンプ数": "Jump Count",
    "合計グリット": "Total Grit",
    "平均フロー": "Average Flow",
    "フラグが立てられています": "Flagged",
    "未舗装路の距離": "Dirt Distance",
    "新規探索した距離": "Newly Explored Distance",
    "新規探索した未舗装路の距離": "Newly Explored Dirt Distance",
    # ==== カロリー・その他 ====
    "カロリー": "Calories",
    "ラン数": "Number of Runs",
    "通勤": "Commute",
    "CO2の削減量": "Carbon Savings",
    "プールの長さ": "Pool Length",
    "アクティビティ数": "Activity Count",
    "ステップ合計": "Step Count",
    "メディア": "Media",
    # ==== その他 ====
    "アップロードより": "Weather Observed",
    "合計サイクル": "Total Cycles",
}

def build_rename_map(columns):
    """重複列（例: '距離', '距離.1'）にも対応したリネーム辞書を作成"""
    rename = {}
    for col in columns:
        base = col.split(".")[0]           # 例: '距離'
        suffix = col[len(base):]           # '' もしくは '.1'
        if base in JP2EN:
            rename[col] = JP2EN[base] + suffix
    return rename

def convert_headers(src: Path, dst: Path):
    df = pd.read_csv(src)
    df = df.rename(columns=build_rename_map(df.columns))
    df.to_csv(dst, index=False)
    print(f"✅ {src.name} -> {dst.name} へ変換完了")

# --- 実行 -------------------------------------------------------
if not SRC.exists():
    raise FileNotFoundError(f"CSV not found: {SRC.resolve()}")

convert_headers(SRC, DST)


✅ activities.csv -> activities.csv へ変換完了


In [13]:
df = pd.read_csv("StravaData/activities.csv", parse_dates=["Activity Date"])

In [14]:
df = pd.read_csv(
    "activities_en.csv",
    parse_dates=["Activity Date"],   # 日付列を datetime へ
    dtype={
        "Distance": "float32",
        "Elapsed Time": "int32",
        "Moving Time": "int32",
    }
)

FileNotFoundError: [Errno 2] No such file or directory: 'activities_en.csv'

In [16]:
df = pd.read_csv(
    "/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/StravaData/activities.csv",
    parse_dates=["Activity Date"],
    thousands=",",           # ← カンマを数値から自動除去
    low_memory=False         # dtype 混在警告を抑制したい場合
)

# 別セルで型を落とす（省メモリ化）
df = df.astype({
    "Distance": "float32",
    "Elapsed Time": "int32",
    "Moving Time": "int32"
})

df.head()

Activity ID       Activity Date Activity Name Activity Type  Description  \
0   8280988291 2022-12-23 06:57:23      午後のランニング         ランニング          NaN   
1   8286585787 2022-12-24 09:57:04         夕方の水泳            水泳          NaN   
2   8293206227 2022-12-26 10:42:37         夕方の水泳            水泳          NaN   
3   8314368113 2022-12-31 06:05:56        午後のライド           ライド          NaN   
4   8330224933 2023-01-01 06:53:06        午後のライド           ライド          NaN   

   Elapsed Time  Distance  Max Heart Rate  Relative Effort  Commute  ...  \
0          1530      4.62             NaN              NaN    False  ...   
1          4454   1150.00             NaN              NaN    False  ...   
2          4556    550.00             NaN              NaN    False  ...   
3          1897      9.10             NaN              NaN    False  ...   
4          1222      7.62             NaN              NaN    False  ...   

   Activity Count  Step Count Carbon Savings  Pool Length  Training Load  \
0             NaN         NaN            NaN          NaN            NaN   
1             NaN         NaN            NaN          NaN            NaN   
2             NaN         NaN            NaN          NaN            NaN   
3             NaN         NaN            NaN          NaN            NaN   
4             NaN         NaN            NaN          NaN            NaN   

   Intensity  Grade Adjusted Pace (Average)  Timer Time  Total Cycles  Media  
0        NaN                            NaN         NaN           NaN    NaN  
1        NaN                            NaN         NaN           NaN    NaN  
2        NaN                            NaN         NaN           NaN    NaN  
3        NaN                            NaN         NaN           NaN    NaN  
4        NaN                            NaN         NaN           NaN    NaN  

[5 rows x 94 columns]

In [17]:
# 0) 前ステップで df に distance_km, moving_hr などが出来ている前提
import pandas as pd
LTHR = 165          # 自分で設定

# 1) intensity_level
df["intensity_level"] = (df["Average Heart Rate"] / LTHR).round(2)

# 2) training_category
bins   = [0, .79, .89, .95, 1.10]
labels = ["Z1-2", "Z3", "Z4", "Z5"]
df["training_category"] = pd.cut(
    df["intensity_level"], bins=bins, labels=labels, right=False
).cat.add_categories("NoHR").fillna("NoHR")

# 3) TRIMP
df["trimp"] = df["moving_hr"] * df["intensity_level"] * 50

# 4) 保存
df.to_parquet("strava_master_enhanced.parquet", index=False)


KeyError: 'moving_hr'

In [18]:
print(df.columns.tolist())


['Activity ID', 'Activity Date', 'Activity Name', 'Activity Type', 'Description', 'Elapsed Time', 'Distance', 'Max Heart Rate', 'Relative Effort', 'Commute', 'Activity Private Notes', 'Gear', 'Filename', 'Athlete Weight', 'Bike Weight', 'Elapsed Time.1', 'Moving Time', 'Distance.1', 'Max Speed', 'Average Speed', 'Elevation Gain', 'Elevation Loss', 'Min Elevation', 'Max Elevation', 'Max Grade', 'Average Grade', 'Average Positive Grade', 'Average Negative Grade', 'Max Cadence', 'Average Cadence', 'Max Heart Rate.1', 'Average Heart Rate', 'Max Power', 'Average Power', 'Calories', 'Max Temperature', 'Average Temperature', 'Relative Effort.1', 'Total Work', 'Number of Runs', 'Uphill Time', 'Downhill Time', 'Other Time', 'Perceived Exertion', 'Device Type', 'Start Time', 'Weighted Average Power', 'Power Count', 'Perceived Exertion Used', 'Perceived Relative Effort', 'Commute.1', 'Total Weight', 'Weather Observed', 'Grade Adjusted Pace', 'Observation Time', 'Weather', 'Average Temperature.1',

In [19]:
# Moving Time は秒なので h に変換
df["moving_hr"] = pd.to_numeric(df["Moving Time"], errors="coerce") / 3600


In [20]:
# --- moving_hr を作ってから一気に ---
LTHR = 165

df = (
    df
    .assign(
        moving_hr       = pd.to_numeric(df["Moving Time"], errors="coerce") / 3600,
        intensity_level = lambda x: (x["Average Heart Rate"] / LTHR).round(2)
    )
)

bins   = [0, .79, .89, .95, 1.10]
labels = ["Z1-2", "Z3", "Z4", "Z5"]
df["training_category"] = pd.cut(
    df["intensity_level"], bins=bins, labels=labels, right=False
).cat.add_categories("NoHR").fillna("NoHR")

df["trimp"] = df["moving_hr"] * df["intensity_level"] * 50


In [22]:
from pathlib import Path

# ----------------------------------------
# 0) 保存先ディレクトリを用意（無ければ作成）
out_dir = Path("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/my_strava_dataset")
out_dir.mkdir(exist_ok=True)

# ----------------------------------------
# 1) Parquet 保存（高速・省サイズ）
parq_path = out_dir / "strava_master_enhanced.parquet"
df.to_parquet(parq_path, index=False)
print(f"✅ Parquet 保存完了: {parq_path}")

# 2) CSV も欲しい場合（任意）
csv_path = out_dir / "strava_master_enhanced.csv"
df.to_csv(csv_path, index=False)
print(f"✅ CSV 保存完了: {csv_path}")


ImportError: Unable to find a usable engine; tried using: 'pyarrow', 'fastparquet'.
A suitable version of pyarrow or fastparquet is required for parquet support.
Trying to import the above resulted in these errors:
 - Missing optional dependency 'pyarrow'. pyarrow is required for parquet support. Use pip or conda to install pyarrow.
 - Missing optional dependency 'fastparquet'. fastparquet is required for parquet support. Use pip or conda to install fastparquet.

In [23]:
!pip install --quiet pyarrow

In [24]:
from pathlib import Path

# ----------------------------------------
# 0) 保存先ディレクトリを用意（無ければ作成）
out_dir = Path("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/my_strava_dataset")
out_dir.mkdir(exist_ok=True)

# ----------------------------------------
# 1) Parquet 保存（高速・省サイズ）
parq_path = out_dir / "strava_master_enhanced.parquet"
df.to_parquet(parq_path, index=False)
print(f"✅ Parquet 保存完了: {parq_path}")

# 2) CSV も欲しい場合（任意）
csv_path = out_dir / "strava_master_enhanced.csv"
df.to_csv(csv_path, index=False)
print(f"✅ CSV 保存完了: {csv_path}")


✅ Parquet 保存完了: /Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/my_strava_dataset/strava_master_enhanced.parquet
✅ CSV 保存完了: /Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/my_strava_dataset/strava_master_enhanced.csv


In [25]:
test = pd.read_parquet(parq_path)
print(test.shape, "rows x columns")
test.head()


(474, 98) rows x columns


Activity ID       Activity Date Activity Name Activity Type  Description  \
0   8280988291 2022-12-23 06:57:23      午後のランニング         ランニング          NaN   
1   8286585787 2022-12-24 09:57:04         夕方の水泳            水泳          NaN   
2   8293206227 2022-12-26 10:42:37         夕方の水泳            水泳          NaN   
3   8314368113 2022-12-31 06:05:56        午後のライド           ライド          NaN   
4   8330224933 2023-01-01 06:53:06        午後のライド           ライド          NaN   

   Elapsed Time  Distance  Max Heart Rate  Relative Effort  Commute  ...  \
0          1530      4.62             NaN              NaN    False  ...   
1          4454   1150.00             NaN              NaN    False  ...   
2          4556    550.00             NaN              NaN    False  ...   
3          1897      9.10             NaN              NaN    False  ...   
4          1222      7.62             NaN              NaN    False  ...   

   Training Load  Intensity Grade Adjusted Pace (Average)  Timer Time  \
0            NaN        NaN                           NaN         NaN   
1            NaN        NaN                           NaN         NaN   
2            NaN        NaN                           NaN         NaN   
3            NaN        NaN                           NaN         NaN   
4            NaN        NaN                           NaN         NaN   

   Total Cycles  Media  intensity_level  training_category  moving_hr  trimp  
0           NaN    NaN              NaN               NoHR   0.421944    NaN  
1           NaN    NaN              NaN               NoHR   0.446111    NaN  
2           NaN    NaN              NaN               NoHR   0.400278    NaN  
3           NaN    NaN              NaN               NoHR   0.454722    NaN  
4           NaN    NaN              NaN               NoHR   0.325278    NaN  

[5 rows x 98 columns]

In [26]:
root = Path("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/my_strava_dataset")
df = pd.read_parquet(root / "strava_master_enhanced.parquet")

In [27]:
df["year"]  = df["date"].dt.year
df["week"]  = df["date"].dt.isocalendar().week
df["month"] = df["date"].dt.month

KeyError: 'date'

In [28]:
print(df.columns.tolist()[:15])   # 列名をざっと表示


['Activity ID', 'Activity Date', 'Activity Name', 'Activity Type', 'Description', 'Elapsed Time', 'Distance', 'Max Heart Rate', 'Relative Effort', 'Commute', 'Activity Private Notes', 'Gear', 'Filename', 'Athlete Weight', 'Bike Weight']


In [29]:
df = df.rename(columns={"Activity Date": "date"})   # 列名が違えば適宜変更
df["date"] = pd.to_datetime(df["date"])             # 念のため datetime 型へ


In [30]:
df["year"]  = df["date"].dt.year
df["week"]  = df["date"].dt.isocalendar().week
df["month"] = df["date"].dt.month

In [31]:
weekly_sport = (
    df.groupby(["year", "week", "Activity Type"], as_index=False)
      .agg(total_dur_hr=("moving_hr", "sum"),
           dist_km      =("distance_km", "sum"),
           trimp_sum    =("trimp", "sum"))
)


KeyError: "Column(s) ['distance_km'] do not exist"

In [32]:
print([c for c in df.columns if "Distance" in c])

['Distance', 'Distance.1', 'Dirt Distance', 'Newly Explored Distance', 'Newly Explored Dirt Distance']


In [33]:
if "Distance" in df.columns:
    df["distance_km"] = pd.to_numeric(df["Distance"], errors="coerce") / 1000
else:
    raise KeyError("Distance 列が見つかりません。列名を確認してください。")

In [34]:
weekly_sport = (
    df.groupby(["year", "week", "Activity Type"], as_index=False)
      .agg(total_dur_hr=("moving_hr", "sum"),
           dist_km      =("distance_km", "sum"),
           trimp_sum    =("trimp", "sum"))
)
weekly_sport.head()

year  week Activity Type  total_dur_hr  dist_km  trimp_sum
0  2022    51         ランニング      0.421944  0.00462        0.0
1  2022    51            水泳      0.446111  1.15000        0.0
2  2022    52           ライド      0.454722  0.00910        0.0
3  2022    52            水泳      0.400278  0.55000        0.0
4  2023     1    ウェイトトレーニング      1.250278  0.00000        0.0

In [1]:
print(df.shape)

NameError: name 'df' is not defined

In [2]:
df = pd.read_parquet("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/my_strava_dataset/strava_master_enhanced.parquet")

NameError: name 'pd' is not defined

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt      # 軽い可視化用



ModuleNotFoundError: No module named 'matplotlib'

In [4]:
import pandas as pd
import numpy as np

In [6]:
df = pd.read_parquet("/Users/jitsugen/Documents/SoloPRJ/Strava-Dataset-PRJ/my_strava_dataset/strava_master_enhanced.parquet")


In [7]:
print(df.shape)

(474, 98)


In [8]:
print(df.columns.tolist())

['Activity ID', 'Activity Date', 'Activity Name', 'Activity Type', 'Description', 'Elapsed Time', 'Distance', 'Max Heart Rate', 'Relative Effort', 'Commute', 'Activity Private Notes', 'Gear', 'Filename', 'Athlete Weight', 'Bike Weight', 'Elapsed Time.1', 'Moving Time', 'Distance.1', 'Max Speed', 'Average Speed', 'Elevation Gain', 'Elevation Loss', 'Min Elevation', 'Max Elevation', 'Max Grade', 'Average Grade', 'Average Positive Grade', 'Average Negative Grade', 'Max Cadence', 'Average Cadence', 'Max Heart Rate.1', 'Average Heart Rate', 'Max Power', 'Average Power', 'Calories', 'Max Temperature', 'Average Temperature', 'Relative Effort.1', 'Total Work', 'Number of Runs', 'Uphill Time', 'Downhill Time', 'Other Time', 'Perceived Exertion', 'Device Type', 'Start Time', 'Weighted Average Power', 'Power Count', 'Perceived Exertion Used', 'Perceived Relative Effort', 'Commute.1', 'Total Weight', 'Weather Observed', 'Grade Adjusted Pace', 'Observation Time', 'Weather', 'Average Temperature.1',

In [9]:
df.head()

Activity ID       Activity Date Activity Name Activity Type  Description  \
0   8280988291 2022-12-23 06:57:23      午後のランニング         ランニング          NaN   
1   8286585787 2022-12-24 09:57:04         夕方の水泳            水泳          NaN   
2   8293206227 2022-12-26 10:42:37         夕方の水泳            水泳          NaN   
3   8314368113 2022-12-31 06:05:56        午後のライド           ライド          NaN   
4   8330224933 2023-01-01 06:53:06        午後のライド           ライド          NaN   

   Elapsed Time  Distance  Max Heart Rate  Relative Effort  Commute  ...  \
0          1530      4.62             NaN              NaN    False  ...   
1          4454   1150.00             NaN              NaN    False  ...   
2          4556    550.00             NaN              NaN    False  ...   
3          1897      9.10             NaN              NaN    False  ...   
4          1222      7.62             NaN              NaN    False  ...   

   Training Load  Intensity Grade Adjusted Pace (Average)  Timer Time  \
0            NaN        NaN                           NaN         NaN   
1            NaN        NaN                           NaN         NaN   
2            NaN        NaN                           NaN         NaN   
3            NaN        NaN                           NaN         NaN   
4            NaN        NaN                           NaN         NaN   

   Total Cycles  Media  intensity_level  training_category  moving_hr  trimp  
0           NaN    NaN              NaN               NoHR   0.421944    NaN  
1           NaN    NaN              NaN               NoHR   0.446111    NaN  
2           NaN    NaN              NaN               NoHR   0.400278    NaN  
3           NaN    NaN              NaN               NoHR   0.454722    NaN  
4           NaN    NaN              NaN               NoHR   0.325278    NaN  

[5 rows x 98 columns]

In [10]:
df.info() 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 474 entries, 0 to 473
Data columns (total 98 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   Activity ID                    474 non-null    int64         
 1   Activity Date                  474 non-null    datetime64[ns]
 2   Activity Name                  474 non-null    object        
 3   Activity Type                  474 non-null    object        
 4   Description                    0 non-null      float64       
 5   Elapsed Time                   474 non-null    int32         
 6   Distance                       474 non-null    float32       
 7   Max Heart Rate                 0 non-null      float64       
 8   Relative Effort                0 non-null      float64       
 9   Commute                        474 non-null    bool          
 10  Activity Private Notes         0 non-null      float64       
 11  Gear               